In [1]:
from huggingface_hub import login
import os 
import torch
torch.cuda.empty_cache()

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

# Use your Hugging Face token here
login("")

from vllm import LLM, SamplingParams


TEXT_LLM_MODEL_MISTRAL='meta-llama/Meta-Llama-3.1-8B-Instruct'



vllm_model = LLM(
        model=TEXT_LLM_MODEL_MISTRAL,
        tensor_parallel_size=1,         # Use both GPUs
        gpu_memory_utilization=0.95,     # Lower memory utilization to prevent OOM
        max_model_len=26000)
        
    


/home/ady/miniconda3/envs/vllm_env/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: fineGrained).
Your token has been saved to /home/ady/.cache/huggingface/token
Login successful


2024-09-15 15:22:07,933	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


INFO 09-15 15:22:08 llm_engine.py:223] Initializing an LLM engine (v0.6.1.post2) with config: model='meta-llama/Meta-Llama-3.1-8B-Instruct', speculative_config=None, tokenizer='meta-llama/Meta-Llama-3.1-8B-Instruct', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, rope_scaling=None, rope_theta=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.bfloat16, max_seq_len=26000, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='outlines'), observability_config=ObservabilityConfig(otlp_traces_endpoint=None, collect_model_forward_time=False, collect_model_execute_time=False), seed=0, served_model_name=meta-llama/Meta-Llama-3.1-8B-Instruct, use_v2_block_manager=False, num_scheduler_steps=1, e

Loading safetensors checkpoint shards:   0% Completed | 0/4 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  25% Completed | 1/4 [00:00<00:00,  6.32it/s]
Loading safetensors checkpoint shards:  50% Completed | 2/4 [00:00<00:00,  2.16it/s]
Loading safetensors checkpoint shards:  75% Completed | 3/4 [00:01<00:00,  1.72it/s]
Loading safetensors checkpoint shards: 100% Completed | 4/4 [00:02<00:00,  1.58it/s]
Loading safetensors checkpoint shards: 100% Completed | 4/4 [00:02<00:00,  1.77it/s]


INFO 09-15 15:22:12 model_runner.py:1008] Loading model weights took 14.9888 GB


INFO 09-15 15:22:15 gpu_executor.py:122] # GPU blocks: 13724, # CPU blocks: 2048
INFO 09-15 15:22:17 model_runner.py:1311] Capturing the model for CUDA graphs. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 09-15 15:22:17 model_runner.py:1315] CUDA graphs can take additional 1~3 GiB memory per GPU. If you are running out of memory, consider decreasing `gpu_memory_utilization` or enforcing eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INFO 09-15 15:22:26 model_runner.py:1430] Graph capturing finished in 10 secs.


In [2]:
# !pwd

: 

Router Data Creation 

In [2]:
import pandas as pd
import numpy as np

NUM_EXAMPLES=200

router_tagged_df=pd.read_csv('/home/ady/Stockbuzz.ai_Data/RouterNER/Router_Tagging.csv')[1:].drop(['Others','NotesForOthers'],axis=1).fillna(0)
router_tagged_df=router_tagged_df[router_tagged_df['AdyTagged']==1]
router_tagged_df=router_tagged_df.drop(['AdyTagged'],axis=1).drop_duplicates()

router_tagged_df = router_tagged_df.melt(id_vars=['username', 'question'], var_name='category', value_name='values')
router_tagged_df=router_tagged_df.sample(frac=1).reset_index(drop=True)
router_tagged_df=router_tagged_df.rename(columns={'question':'text'})
router_tagged_df=router_tagged_df[router_tagged_df['values']==1]


router_tagged_df_sample=router_tagged_df[0:NUM_EXAMPLES]
router_tagged_df_sample


username  \
0     4b0d73e8-6ac2-4214-8c68-7d1fc36dd12d   
2     0f52d06c-09d2-4c99-8faa-9ec98808ae02   
3     ed2ece58-3ce3-4cb9-a013-2e569bb14fcf   
6     5ce399be-648c-4768-8e25-a73ca480d4e2   
11    f760f937-be70-4ab6-9ad8-3b69edae7a76   
...                                    ...   
1042  18776314-d3b4-4fd4-a328-991b448c8a3c   
1043  17e24d74-ce34-4c80-a4b0-00f91021e28a   
1064  044fdc80-40d2-4322-8c5a-749bdb1c651d   
1072  3c484112-d34d-459f-8e03-33d488088e4b   
1091  f4fccd78-2c2a-4d97-9df6-d5504d87ee7e   

                                                   text         category  \
0      What’s is the P/E of CVS compared to competitors  CompanyAnalysis   
2     How does Cigar-Butt Investing differ from othe...              LLM   
3     tell me a stock which will increase by 5 % in ...       OutOfScope   
6                              Is MTCH revenue growing?  CompanyAnalysis   
11                          What is Momentum investing?              LLM   
...                                                 ...              ...   
1042  What is the intrinsic value of Brookfield corp...  CompanyAnalysis   
1043  Build me a stock portfolio before general elec...       OutOfScope   
1064  Which sectors are most affected by economic cy...              LLM   
1072  what do you know about the sentiment of intel ...  CompanyAnalysis   
1091                                                 Hi       OutOfScope   

      values  
0        1.0  
2        1.0  
3        1.0  
6        1.0  
11       1.0  
...      ...  
1042     1.0  
1043     1.0  
1064     1.0  
1072     1.0  
1091     1.0  

[200 rows x 4 columns]

In [ ]:
import pandas as pd
import os

pd.set_option('max_colwidth', 1400)

# Select a subset of the data
all_questions = router_tagged_df_sample['text'].values.tolist()

synthetic_questions_dict = {}
all_prompts = []
original_prompts = []  # To keep track of the original prompts

for prompt in all_questions:
    Instruction = f"""<s>[INST] Imagine you are an expert & award winning stock market analyst who specializes in asking the right questions relevant to a thorough stock research. Given a user query, generate 20 further precise, expert and relevant questions with focus on identifying similar companies related to the given query. I want exactly 20 questions. Your questions should be all-encompassing and can be answered independently. Don't use words like 'GIVEN QUERY' or 'GIVEN INDUSTRY'. If an industry or sector is provided, try to respond with diverse questions with similar sectors pertinent to financial markets. If a ratio like MarketCap or ROI is asked in the question, your response should have a slightly different ratio based on your stock market understanding. The questions should be brief and less than 20 words. If there is a company name mentioned in the question, please use the same company name (with paraphrasing as needed) in related questions. QUESTION: {prompt} Start with similar questions directly without any note or disclaimer.[/INST]"""
    all_prompts.append(Instruction)
    original_prompts.append(prompt)

# Repeat the prompts for multiple iterations
all_prompts = all_prompts * 3
original_prompts = original_prompts * 3

# Define the sampling parameters
sampling_params = SamplingParams(temperature=0.3, max_tokens=1200)

# Generate outputs using the model
outputs = vllm_model.generate(all_prompts, sampling_params)

# Process the generated outputs and store them in a dictionary
synthetic_questions_dict = {}
for output, original_prompt in zip(outputs, original_prompts):
    generated_text = output.outputs[0].text.strip() if output.outputs else 'N/A'
    similar_questions = generated_text.split('\n')
    if original_prompt in synthetic_questions_dict:
            synthetic_questions_dict[original_prompt].extend(similar_questions)
    else:
        synthetic_questions_dict[original_prompt] = similar_questions

# Convert the dictionary to a DataFrame
synthetic_questions_df = pd.DataFrame(list(synthetic_questions_dict.items()), columns=['text', 'Questions'])

# Explode the list of questions into separate rows
synthetic_questions_df = synthetic_questions_df.explode('Questions')

# Merge with the original DataFrame to include the 'category' column
synthetic_questions_df = synthetic_questions_df.merge(router_tagged_df_sample[['text', 'category']], on='text').sample(frac=1)

# Remove duplicates
synthetic_questions_df = synthetic_questions_df.drop_duplicates()

# Ensure the directory exists
output_directory = "/home/ady/Stockbuzz.ai_Data/RouterNER/"
os.makedirs(output_directory, exist_ok=True)

# Save the DataFrame to the specified CSV file location
output_file_path = os.path.join(output_directory, "synthetic_questions_df.csv")
synthetic_questions_df.to_csv(output_file_path, index=False)

# Display the final DataFrame
synthetic_questions_df


Processed prompts:   0%|          | 0/600 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

RuntimeError: LLMEngine should not be pickled!

 Router Model

In [2]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
import numpy as np
import pandas as pd
import torch
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from sklearn.metrics import precision_recall_fscore_support, accuracy_score
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments, EarlyStoppingCallback
import gc
import random
import json
import os

# Set device to GPU 0
device = torch.device("cuda:0")

# Clear GPU memory
torch.cuda.empty_cache()
gc.collect()

# Load the training DataFrame
synthetic_questions_df = pd.read_csv("/home/ady/Stockbuzz.ai_Data/RouterNER/synthetic_questions_df.csv")

# Updating Training Data in same format
question_dict = synthetic_questions_df.groupby('text')['Questions'].apply(list).to_dict()

# Function to create 'Question_Concatenate'
def create_question_concatenate(row):
    primary_key = row['text']
    possible_values = question_dict[primary_key]
    if len(possible_values) < 2:
        selected_items = possible_values
    else:
        selected_items = random.sample(possible_values, 2)
    return f"{row['text']},{row['Questions']},{selected_items[0]},{selected_items[1]}"

# Apply the function to create the new column
synthetic_questions_df['Questions'] = synthetic_questions_df.apply(create_question_concatenate, axis=1)
synthetic_questions_df['label'] = synthetic_questions_df['category'].astype('category').cat.codes

# synthetic_questions_df=synthetic_questions_df.sample(n=min(100,len(synthetic_questions_df)))

# Create the category-to-label mapping
label_to_category = dict(enumerate(synthetic_questions_df['category'].astype('category').cat.categories))
category_to_label = {v: k for k, v in label_to_category.items()}

# Save the mapping to a JSON file in the model's directory
os.makedirs('Router_Models', exist_ok=True)
with open('Router_Models/label_to_category.json', 'w') as f:
    json.dump(label_to_category, f)
with open('Router_Models/category_to_label.json', 'w') as f:
    json.dump(category_to_label, f)

# Split data based on unique 'text'
unique_sql_all = synthetic_questions_df['text'].unique().tolist()
train_size = int(0.8 * len(unique_sql_all))
val_size = int(0.2 * len(unique_sql_all))

train_sqls = unique_sql_all[:train_size]
val_sqls = unique_sql_all[train_size:train_size + val_size]

train_df = synthetic_questions_df[synthetic_questions_df['text'].isin(train_sqls)]
val_df = synthetic_questions_df[synthetic_questions_df['text'].isin(val_sqls)]

# Initialize the tokenizer
EMBEDDING_MODEL = 'google-bert/bert-large-uncased'
tokenizer = BertTokenizer.from_pretrained(EMBEDDING_MODEL)

# Tokenize the datasets
def tokenize_data(data):
    return tokenizer(data['Questions'].astype(str).tolist(), padding=True, truncation=True, max_length=128, return_tensors='pt')

train_tokens = tokenize_data(train_df)
val_tokens = tokenize_data(val_df)

train_labels = torch.tensor(train_df['label'].values, dtype=torch.long)
val_labels = torch.tensor(val_df['label'].values, dtype=torch.long)

# Create custom Dataset class
class ArticleDataset(Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels

    def __getitem__(self, idx):
        item = {key: val[idx] for key, val in self.encodings.items()}
        item['labels'] = self.labels[idx]
        return item

    def __len__(self):
        return len(self.labels)

train_dataset = ArticleDataset(train_tokens, train_labels)
val_dataset = ArticleDataset(val_tokens, val_labels)

# Load the model
model = BertForSequenceClassification.from_pretrained(EMBEDDING_MODEL, num_labels=train_df['label'].nunique())
model.to(device)  # Move the model to the specified device

# Define the compute_metrics function
def compute_metrics(p):
    preds = np.argmax(p.predictions, axis=1)
    labels = p.label_ids
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='weighted')
    acc = accuracy_score(labels, preds)
    return {
        'accuracy': acc,
        'precision': precision,
        'recall': recall,
        'f1': f1,
    }

# Define the training arguments
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=10,
    per_device_train_batch_size=64,
    per_device_eval_batch_size=64,
    gradient_accumulation_steps=4,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    save_total_limit=1,
    no_cuda=False,
    dataloader_pin_memory=False,
)

# Define the trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    compute_metrics=compute_metrics,
    callbacks=[EarlyStoppingCallback(early_stopping_patience=3)],
)

# Train the model
trainer.train()

# Save the model to the specified directory
model.save_pretrained('/home/ady/Stockbuzz.ai_Models/RouterNER/Router_Models/')
tokenizer.save_pretrained('/home/ady/Stockbuzz.ai_Models/RouterNER/Router_Models/')


/home/ady/miniconda3/envs/vllm_env/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed intern

OutOfMemoryError: CUDA out of memory. Tried to allocate 16.00 MiB. GPU 0 has a total capacity of 47.42 GiB of which 6.38 MiB is free. Process 2320625 has 260.00 MiB memory in use. Process 2325452 has 260.00 MiB memory in use. Process 2328697 has 260.00 MiB memory in use. Process 2334035 has 260.00 MiB memory in use. Process 2398498 has 45.27 GiB memory in use. Including non-PyTorch memory, this process has 1.06 GiB memory in use. Of the allocated memory 810.76 MiB is allocated by PyTorch, and 11.24 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

: 

Router Inference

In [3]:
import torch
from transformers import BertTokenizer, BertForSequenceClassification
import openai
import pandas as pd
import json
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity

# # Initialize OpenAI API client
# OPEN_AI_API_KEY = "EMPTY"
# OPENAI_API_BASE_MISTRAL = "http://0.0.0.0:8000/v1"
# client_mistral = openai.OpenAI(api_key=OPEN_AI_API_KEY, base_url=OPENAI_API_BASE_MISTRAL)

# TEXT_LLM_MODEL_MISTRAL = 'mistralai/Mistral-7B-Instruct-v0.2'

# Load the model and tokenizer
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_router = BertForSequenceClassification.from_pretrained('/home/ady/Stockbuzz.ai_Models/RouterNER/Router_Models')
tokenizer_router = BertTokenizer.from_pretrained('/home/ady/Stockbuzz.ai_Models/RouterNER//Router_Models')
model_router.to(device)  # Move the model to the specified device

# Load the category-to-label mapping
with open('Router_Models/label_to_category.json', 'r') as f:
    label_to_category_router = json.load(f)



def predict_router(text):
    model_router.eval()
    inputs = tokenizer_router(text, return_tensors='pt', padding=True, truncation=True, max_length=128).to(device)
    with torch.no_grad():
        outputs = model_router(**inputs)
    logits = outputs.logits
    predicted_class_id = logits.argmax().item()
    return label_to_category_router[str(predicted_class_id)]

def reformulate_query(question):
    """Reformulate the given question using OpenAI API."""
    INSTRUCTION = f"""<s>[INST] Imagine you are an expert & award-winning stock market analyst who specializes in asking the right questions relevant for thorough stock research. 
    Given a user query, generate 3 further precise, expert, and relevant questions. 
    I want exactly 3 questions. Don't use words like 'GIVEN QUERY' or 'GIVEN INDUSTRY'. 
    If an industry or sector is provided, try to respond with diverse questions with similar sectors pertinent to financial markets. 
    If a ratio like MarketCap or ROI is asked in the question, your response should have a slightly different ratio based on your stock market understanding. 
    The questions should be brief and less than 20 words. If there is a company name mentioned in the question, please use the same company name (with paraphrasing as needed) in related questions.
    If the question is asking about non-US stocks, please be explicit in the country name based on your knowledge. 
    Don't change the intent of related questions, e.g., data-seeking question vs. knowledge-seeking question. QUESTION: {question} Start with similar questions directly without any note or disclaimer.[/INST]"""

    # response = client_mistral.chat.completions.create(
    #     model=TEXT_LLM_MODEL_MISTRAL,
    #     messages=[{"role": "user", "content": INSTRUCTION}],
    #     max_tokens=100,
    #     temperature=0.2
    # )
    # content = response.choices[0].message.content
    # reformulated_query = question + ", Related Question:" + content
    
    # return reformulated_query

    sampling_params = SamplingParams(temperature=0.2, max_tokens=100)
    outputs = vllm_model.generate([INSTRUCTION], sampling_params=sampling_params)
    
    generated_text = outputs[0].outputs[0].text.strip()  # Get the generated text from the model
    reformulated_query = question + ", Related Question: " + generated_text
    
    return reformulated_query

# Example usage:
questions = ["Top 3 companies by market cap?",
             "Compare revenues of Apple vs Micrsoft",
             "Latest revenues of Amazon",
             "Latest revenues of Sun Pharma in India?",
             "which cryptocurrency should I buy?",
             "What is Value investing?",
             "What is AWS Bedrock?","Summarize latest earning call of Nvidia","How long will the a.i frenzy continue?"]
for text in questions:
    print(text)
    reformulated_query_llm = reformulate_query(text)
    category = predict_router(reformulated_query_llm)
    print(f"Category: {category}",'\n')



Top 3 companies by market cap?


Processed prompts: 100%|██████████| 1/1 [00:02<00:00,  2.31s/it, est. speed input: 105.19 toks/s, output: 43.29 toks/s]


Category: SQL 

Compare revenues of Apple vs Micrsoft


Processed prompts: 100%|██████████| 1/1 [00:02<00:00,  2.31s/it, est. speed input: 105.18 toks/s, output: 43.28 toks/s]


Category: CompanyAnalysis 

Latest revenues of Amazon


...

Category: CompanyAnalysis 

Summarize latest earning call of Nvidia


Processed prompts: 100%|██████████| 1/1 [00:02<00:00,  2.32s/it, est. speed input: 104.94 toks/s, output: 43.18 toks/s]


Category: CompanyAnalysis 

How long will the a.i frenzy continue?


Processed prompts: 100%|██████████| 1/1 [00:02<00:00,  2.32s/it, est. speed input: 105.36 toks/s, output: 43.18 toks/s]

Category: RAG 



## Subrouter

SubRouter - Data 

In [ ]:
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "0"


In [ ]:
from huggingface_hub import login
import os 
import torch
torch.cuda.empty_cache()

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

# Use your Hugging Face token here
login("")

from vllm import LLM, SamplingParams


TEXT_LLM_MODEL_MISTRAL='meta-llama/Meta-Llama-3.1-8B-Instruct'



vllm_model = LLM(
        model=TEXT_LLM_MODEL_MISTRAL,
        tensor_parallel_size=1,         # Use both GPUs
        gpu_memory_utilization=0.95,     # Lower memory utilization to prevent OOM
        max_model_len=26000)
        
    


In [ ]:
import pandas as pd
import openai
import aiohttp
import asyncio
import nest_asyncio
import re
pd.set_option('max_colwidth', 2400)


categories = {
    1: {
        "name": "fair valuation",
        "prompt": "As a stock market analyst, generate a set of diverse and comprehensive questions that explore various aspects of determining the fair valuation of a company. These questions should cover methodologies such as discounted cash flow analysis. Ensure the questions address different valuation techniques or whether to buy or sell a stock or fair value of the company or anything about the stock price of a company."
    },
    2: {
        "name": "industry analysis",
        "prompt": "Generate a diverse range of questions aimed at conducting an in-depth analysis of different industries. The questions should cover industry trends, competitive landscape, regulatory impacts, and market opportunities. Include questions that focus on the analysis of industry such as electric vehicle, e-commerce, retail, technology etc."
    },
    3: {
        "name": "single company analysis",
        "prompt": "Create a set of detailed questions that focus on the comprehensive analysis of a single company. These questions should encompass the company's financial health, business model, management effectiveness, market position, and competitive advantages. Ensure the questions cover key financial statements, ratios, and strategic initiatives such as What do you think about Amazon stock."
    },
    4: {
        "name": "multiple companies analysis",
        "prompt": "Generate a variety of questions designed to compare and contrast multiple companies within the same industry or sector. These questions should necessarily have more than 1 company to compare and contrast on single or multiple parameters or same industry or different industry."
    }
}

# Define example questions for each category
example_questions = {
    1: [
        "Will GME's stock price increase today?",
        "Abercrombie is trading at $190 per share; is it a good buy?",
        "What is the intrinsic value of Brookfield Corporation?",
        "Is Dynagas a good stock for the long run?",
        "Is Taiwan Semiconductor a good stock for the long run?",
        "Is it the right time to buy Nvidia stock?",
        "Why is Tesla considered overrated?",
        "What is the intrinsic value of Microsoft based on a discounted cash flow analysis?",
        "How does the price-to-earnings ratio of Amazon compare to its historical average?",
        "What is the fair value of Tesla based on comparable company analysis?",
        "How does the enterprise value to EBITDA ratio of Facebook compare to industry peers?",
        "What is the impact of interest rate changes on the valuation of Apple?",
        "How does the price-to-sales ratio of Google compare to other tech giants?",
        "What is the fair value of Netflix using a precedent transactions analysis?",
        "How do changes in tax policy affect the valuation of Amazon?",
        "What is the intrinsic value of Uber based on a discounted cash flow analysis?",
        "How does the price-to-book ratio of Microsoft compare to its historical average?",
        "What is the fair value of Facebook using a multi-stage growth model?",
        "How do changes in market conditions impact the valuation of Apple?",
        "What is the intrinsic value of Tesla based on a residual income model?",
        "How does the enterprise value to revenue ratio of Amazon compare to its peers?",
        "What is the fair value of Google using an excess earnings model?",
        "How do changes in cost of capital affect the valuation of Netflix?",
        "What is the intrinsic value of Uber based on a real options analysis?",
        "How does the price-to-cash-flow ratio of Microsoft compare to its historical average?",
        "What is the fair value of Facebook using an economic profit model?",
        "How do changes in growth expectations impact the valuation of Tesla?"
    ],
    2: [
        "Will electric vehicles outperform the market this year?",
        "Analyze retail industry for me",
        "Is Artificial Intelligence a hype?",
        "What are the major trends in the e-commerce industry?",
        "How has the renewable energy sector evolved over the past decade?",
        "What are the key drivers of growth in the biotechnology industry?",
        "How has the competitive landscape changed in the automotive industry?",
        "What are the regulatory challenges facing the pharmaceutical industry?",
        "How has the rise of fintech impacted the financial services sector?",
        "What are the growth prospects for the telecommunications industry?",
        "How has the adoption of AI affected the technology sector?",
        "What are the key challenges facing the retail industry?",
        "How has the global supply chain crisis impacted the manufacturing industry?",
        "What are the major trends in the healthcare industry?",
        "How has the rise of streaming services affected the media industry?",
        "What are the key opportunities in the electric vehicle market?",
        "How has the COVID-19 pandemic impacted the travel and tourism industry?",
        "What are the growth drivers for the cybersecurity industry?",
        "How has the real estate market evolved in recent years?",
        "What are the key factors influencing the oil and gas industry?",
        "How has the shift to remote work impacted the tech industry?",
        "What are the major challenges facing the agriculture industry?",
        "How has the rise of social media influenced the advertising industry?"
    ],
    3: [
        "What are the key risks for HRBR?",
        "Analyse the financial health of CVS.",
        "What is the revenue trend for Arch Resources?",
        "Is Amazon a good buy?",
        "Tell me about Amazon's business model.",
        "Analyse the latest earnings call of Meta.",
        "How have Amazon's focus areas changed?",
        "What are the key risks investing in Nvidia?",
        "What are the key risks investing in Starbucks?",
        "What is Starbucks' revenue breakdown?",
        "What is Apple's revenue breakdown?",
        "What is the ROI of Starbucks?",
        "Provide an overview of BYD.",
        "What are the key financial ratios for evaluating Apple's performance?",
        "How has Tesla's market share evolved over the past five years?",
        "What are the major revenue streams for Alphabet (Google)?",
        "What is the impact of recent regulatory changes on Facebook's business?",
        "How does Microsoft's cloud business compare to its other segments?",
        "What are the growth prospects for Netflix in international markets?",
        "What are the key risks associated with investing in Uber?",
        "How has Starbucks' expansion strategy impacted its financial performance?",
        "What are the main factors driving Amazon's profitability?",
        "How has Disney's acquisition strategy affected its financial health?",
        "What are the key financial metrics for evaluating IBM's performance?",
        "How has Twitter's user growth impacted its revenue?",
        "What are the strategic initiatives of Coca-Cola to maintain market leadership?",
        "How has Pfizer's R&D spending influenced its product pipeline?",
        "What are the major cost components for Walmart?",
        "How does Apple's product diversification impact its revenue stability?",
        "What are the competitive advantages of Nvidia in the semiconductor industry?",
        "How has Tesla's focus on autonomous driving technology affected its market position?",
        "What are the financial implications of Google's recent acquisitions?",
        "How has Microsoft's focus on subscription services impacted its revenue?"
    ],
    4: [
        "Compare the fundamentals of AMD and Intel over the last 5 years.",
        "How does Nvidia's profitability compare to other semiconductor companies?",
        "Costco Vs Walmart",
        "How do the financial metrics of Apple compare to those of Samsung?",
        "What are the key differences in business models between Amazon and Alibaba?",
        "How does the profitability of Google compare to Facebook?",
        "What are the growth prospects for Netflix compared to Disney+?",
        "How does the market share of Ford compare to General Motors?",
        "What are the key financial metrics for comparing Coca-Cola and PepsiCo?",
        "How does the revenue growth of Microsoft compare to IBM?",
        "What are the major differences in cost structures between Walmart and Target?",
        "How does the dividend policy of Verizon compare to AT&T?",
        "What are the key financial ratios for comparing ExxonMobil and Chevron?",
        "How does the R&D spending of Intel compare to AMD?",
        "What are the growth strategies of Uber compared to Lyft?",
        "How does the market capitalization of Tesla compare to Ford?",
        "What are the key differences in revenue streams between Netflix and Hulu?",
        "How does the financial performance of Visa compare to Mastercard?",
        "What are the competitive advantages of Nike compared to Adidas?",
        "How does the profitability of Procter & Gamble compare to Unilever?",
        "What are the key financial metrics for comparing JPMorgan Chase and Goldman Sachs?",
        "How does the market share of McDonald's compare to Burger King?",
        "What are the major differences in business strategies between Apple and Microsoft?"
    ]
}

df_list=[]
for category_id, details in categories.items():
        for example_question in example_questions[category_id]:
            for _ in range(100):  # Repeat 10 times
                prompt = f""" Category: {category_id}. You are an expert stock market analyst tasked with creating questions for training a model. Here are some example questions for reference:\n\n{example_question}\n\nNow, generate 1 unique, diverse, and insightful question specifically for {details['name']}. Ensure the question provides significant analytical depth and covers the key aspects outlined. Start generating the questions directly without any preamble. Please remember that you have to generate just one question and stop your response once you have provided the question, Provide question in xml tags i.e <question>...</question>"""
                df_list.append({'Category': details['name'], 'Prompt': prompt})

# Create a DataFrame from the list
full_df = pd.DataFrame(df_list)

prompts=[]
all_questions=full_df['Prompt'].values.tolist()

for question in  all_questions:
    prompts.append(question)

sampling_params = SamplingParams(
        temperature=0.7,
        max_tokens=100
    )

outputs = vllm_model.generate(prompts, sampling_params)

llm_output=[]
for output in outputs:
    try:
        generated_text = output.outputs[0].text
        match = re.search(r'<question>(.*?)</question>', generated_text, re.DOTALL)
        question_text = match.group(1).strip()  # Strips any leading/trailing whitespace


        llm_output.append(question_text)
    except:
        llm_output.append('')


full_df['Response'] =llm_output
display(full_df)
full_df=full_df[full_df['Response']!='']
full_df.to_csv('/home/ady/Stockbuzz.ai_Data/RouterNER/Combined_Ady_Database.csv', index=False)# print("Synthetic questions dataset created and saved to 'Ady_Database4.csv'.")


SubRouter - Model

In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments, EarlyStoppingCallback
import gc
import os
import json

import os

os.environ["CUDA_VISIBLE_DEVICES"] = "1"



# Set device to GPU 0 if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Clear GPU memory
torch.cuda.empty_cache()
gc.collect()

# Load the generated CSV
df = pd.read_csv("/home/ady/Stockbuzz.ai_Data/RouterNER/Combined_Ady_Database.csv")
df = df.sample(n=min(10000,len(df)))

df.rename(columns={'Category': 'category', 'Response': 'Questions'}, inplace=True)

# Create the category-to-label mapping
df['label'] = df['category'].astype('category').cat.codes
label_to_category = dict(enumerate(df['category'].astype('category').cat.categories))
category_to_label = {v: k for k, v in label_to_category.items()}

# Save the mapping to a JSON file in the model's directory
os.makedirs('SubRouter_Models', exist_ok=True)
with open('SubRouter_Models/label_to_category.json', 'w') as f:
    json.dump(label_to_category, f)
with open('SubRouter_Models/category_to_label.json', 'w') as f:
    json.dump(category_to_label, f)

# Split the dataset into training and validation sets based on unique 'Questions'
unique_questions = df['Questions'].unique().tolist()
train_size = int(0.8 * len(unique_questions))
val_size = int(0.2 * len(unique_questions))

train_questions = unique_questions[:train_size]
val_questions = unique_questions[train_size:train_size + val_size]

train_df = df[df['Questions'].isin(train_questions)]
val_df = df[df['Questions'].isin(val_questions)]

# Initialize the BERT tokenizer and model
checkpoint="google-bert/bert-large-uncased"
tokenizer_subrouter = BertTokenizer.from_pretrained(checkpoint)
model_subrouter = BertForSequenceClassification.from_pretrained(checkpoint, num_labels=len(df['category'].unique()))
model_subrouter.to(device)  # Move the model to the specified device

# Tokenize the datasets
def tokenize_data(data):
    return tokenizer_subrouter(data['Questions'].astype(str).tolist(), padding=True, truncation=True, max_length=64, return_tensors='pt')

train_tokens = tokenize_data(train_df)
val_tokens = tokenize_data(val_df)

train_labels = torch.tensor(train_df['label'].values, dtype=torch.long)
val_labels = torch.tensor(val_df['label'].values, dtype=torch.long)

# Create custom Dataset class
class ArticleDataset(torch.utils.data.Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels

    def __getitem__(self, idx):
        item = {key: val[idx] for key, val in self.encodings.items()}
        item['labels'] = self.labels[idx]
        return item

    def __len__(self):
        return len(self.labels)

train_dataset = ArticleDataset(train_tokens, train_labels)
val_dataset = ArticleDataset(val_tokens, val_labels)

# Define the compute_metrics function for evaluation
def compute_metrics(pred):
    labels = pred.label_ids
    preds = pred.predictions.argmax(-1)
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='weighted')
    acc = accuracy_score(labels, preds)
    return {
        'accuracy': acc,
        'precision': precision,
        'recall': recall,
        'f1': f1,
    }

# Define the training arguments
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=5,
    per_device_train_batch_size=128,
    per_device_eval_batch_size=128,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    save_total_limit=1,
    no_cuda=False,
    dataloader_pin_memory=False,
)

# Define the trainer
trainer = Trainer(
    model=model_subrouter,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    compute_metrics=compute_metrics,
    callbacks=[EarlyStoppingCallback(early_stopping_patience=3)],
)

# Train the model
trainer.train()

# Save the model and tokenizer to the specified directory
model_subrouter.save_pretrained('/home/ady/Stockbuzz.ai_Models/RouterNER/SubRouter_Models/')
tokenizer_subrouter.save_pretrained('/home/ady/Stockbuzz.ai_Models/RouterNER/SubRouter_Models/')


/home/ady/miniconda3/envs/vllm_env/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/ady/miniconda3/envs/vllm_env/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed 

('SubRouter_Models/tokenizer_config.json',
 'SubRouter_Models/special_tokens_map.json',
 'SubRouter_Models/vocab.txt',
 'SubRouter_Models/added_tokens.json')

SubRouter Inference

In [2]:
import torch
from transformers import BertTokenizer, BertForSequenceClassification
import json

# Load the model and tokenizer
device = torch.device("cuda")
model_subrouter = BertForSequenceClassification.from_pretrained('./SubRouter_Models')
tokenizer_subrouter = BertTokenizer.from_pretrained('./SubRouter_Models')
model_subrouter.to(device)  # Move the model to the specified device

# Load the category-to-label mapping
with open('SubRouter_Models/label_to_category.json', 'r') as f:
    label_to_category_subrouter = json.load(f)

def predict_subrouter(text):
    model_subrouter.eval()
    inputs = tokenizer_subrouter(text, return_tensors='pt', padding=True, truncation=True, max_length=64).to(device)
    with torch.no_grad():
        outputs = model_subrouter(**inputs)
    logits = outputs.logits
    predicted_class_id = logits.argmax().item()
    return label_to_category_subrouter[str(predicted_class_id)]

# Example usage:
questions = ["Compare depreciation ttm of amazon and intol",
    "What is the current market trend for technology stocks?",
             "How did shakti pumps perform in the last quarter?",
             "Compare Amazon vs Apple in terms of revenues",
             "What is the reasonable price of Nvidia?",
             "Compare Apple vs Micrsoft"]
for text in questions:
    category = predict_subrouter(text)
    print(f"Question: {text}\nPredicted Category: {category}\n")


Question: Compare depreciation ttm of amazon and intol
Predicted Category: multiple companies analysis

Question: What is the current market trend for technology stocks?
Predicted Category: industry analysis

Question: How did shakti pumps perform in the last quarter?
Predicted Category: single company analysis

Question: Compare Amazon vs Apple in terms of revenues
Predicted Category: multiple companies analysis

Question: What is the reasonable price of Nvidia?
Predicted Category: fair valuation

Question: Compare Apple vs Micrsoft
Predicted Category: multiple companies analysis



NER

In [14]:
from huggingface_hub import login
import os 
import torch
torch.cuda.empty_cache()

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

# Use your Hugging Face token here
login("")

from vllm import LLM, SamplingParams


TEXT_LLM_MODEL_MISTRAL='meta-llama/Meta-Llama-3.1-8B-Instruct'



vllm_model = LLM(
        model=TEXT_LLM_MODEL_MISTRAL,
        tensor_parallel_size=1,         # Use both GPUs
        gpu_memory_utilization=0.95,     # Lower memory utilization to prevent OOM
        max_model_len=26000)
        
    


The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: fineGrained).
Your token has been saved to /home/ady/.cache/huggingface/token
Login successful


2024-09-15 21:07:20,332	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


INFO 09-15 21:07:20 llm_engine.py:223] Initializing an LLM engine (v0.6.1.post2) with config: model='meta-llama/Meta-Llama-3.1-8B-Instruct', speculative_config=None, tokenizer='meta-llama/Meta-Llama-3.1-8B-Instruct', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, rope_scaling=None, rope_theta=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.bfloat16, max_seq_len=26000, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='outlines'), observability_config=ObservabilityConfig(otlp_traces_endpoint=None, collect_model_forward_time=False, collect_model_execute_time=False), seed=0, served_model_name=meta-llama/Meta-Llama-3.1-8B-Instruct, use_v2_block_manager=False, num_scheduler_steps=1, e

Loading safetensors checkpoint shards:   0% Completed | 0/4 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  25% Completed | 1/4 [00:00<00:00,  6.39it/s]
Loading safetensors checkpoint shards:  50% Completed | 2/4 [00:00<00:00,  2.18it/s]
Loading safetensors checkpoint shards:  75% Completed | 3/4 [00:01<00:00,  1.74it/s]
Loading safetensors checkpoint shards: 100% Completed | 4/4 [00:02<00:00,  1.59it/s]
Loading safetensors checkpoint shards: 100% Completed | 4/4 [00:02<00:00,  1.77it/s]



INFO 09-15 21:07:24 model_runner.py:1008] Loading model weights took 14.9888 GB
INFO 09-15 21:07:28 gpu_executor.py:122] # GPU blocks: 13756, # CPU blocks: 2048
INFO 09-15 21:07:29 model_runner.py:1311] Capturing the model for CUDA graphs. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 09-15 21:07:29 model_runner.py:1315] CUDA graphs can take additional 1~3 GiB memory per GPU. If you are running out of memory, consider decreasing `gpu_memory_utilization` or enforcing eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.


OutOfMemoryError: CUDA out of memory. Tried to allocate 20.00 MiB. GPU 0 has a total capacity of 47.43 GiB of which 16.69 MiB is free. Including non-PyTorch memory, this process has 47.38 GiB memory in use. Of the allocated memory 46.94 GiB is allocated by PyTorch, with 33.31 MiB allocated in private pools (e.g., CUDA Graphs), and 41.20 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

NER Data Creation

In [16]:
!pip install matplotlib


Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 162.6/162.6 kB 35.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.3/8.3 MB 99.9 MB/s eta 0:00:00ta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 323.2/323.2 kB 134.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.9/4.9 MB 100.0 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 122.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.1/104.1 kB 547.9 MB/s eta 0:00:00


In [18]:
!pip install seqeval


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 249.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for seqeval: filename=seqeval-1.2.2-py3-none-any.whl size=16162 sha256=3ad02021d3334b570a31b1504d9d0c4da3569f9ff09c9efb6da8b2b37276ac87
  Stored in directory: /tmp/pip-ephem-wheel-cache-a6hygjhv/wheels/bc/92/f0/243288f899c2eacdfa8c5f9aede4c71a9bad0ee26a01dc5ead
Successfully built seqeval


In [ ]:
import os
import pandas as pd
import aiohttp
import asyncio
import nest_asyncio
import random
import re
pd.set_option('max_colwidth', 2400)

# # Apply the nest_asyncio patch
# nest_asyncio.apply()

# # Set environment variables
# OPEN_AI_API_KEY = "EMPTY"  # Replace with your actual API key
# OPENAI_API_BASE_MIXTRAL = os.getenv("OPENAI_API_BASE_MIXTRAL", "http://0.0.0.0:8004/v1")
# TEXT_LLM_MODEL_MIXTRAL = 'cognitivecomputations/dolphin-2.8-mistral-7b-v02'

# List of metrics to be included in questions
metrics = [
    "Return on Capital Employed",
    "Debt ratio",
    "Debt-Equity ratio",
    "Interest Coverage",
    "Dividend Payout ratio",
    "PE Ratio",
    "PE to Growth ratio",
    "Dividend yield",
    "Enterprise Value Multiple",
    "Dividend yield TTM",
    "Dividend yield percentage TTM",
    "PE ratio TTM",
    "PEF ratio TTM",
    "Current ratio TTM",
    "Quick ratio TTM",
    "Gross Profit Margin TTM",
    "Operating Profit Margin TTM",
    "Net-Profit Margin TTM",
    "Return on Assets TTM",
    "Return on Equity TTM",
    "Return on Capital Employed TTM",
    "Debt ratio TTM",
    "Debt-Equity ratio TTM",
    "Interest Coverage TTM",
    "PE ratio TTM",
    "PEG ratio TTM",
    "Price to Sales ratio TTM",
    "Price to Fair-Value TTM",
    "Dividend per share TTM",
    "Revenue growth",
    "EBITDA growth",
    "Net-Income growth",
    "Growth in Net-Income-ratio",
    "EPS growth",
    "Total-Debt growth",
    "NetDebt growth",
    "Altman Z Score",
    "Piotroski Score",
    "Working Capital",
    "Total Assets",
    "Retained Earnings",
    "EBIT",
    "Total Liabilities"
]

# List of entities (companies) to be included in questions
entities = [
    "Amazon", "Apple", "Microsoft", "Google", "Facebook", "Nvidia",
    "Meta", "Tesla", "Broadcom", "ASML", "Costco", "Cisco", "Intel", "Adobe"
]

# New list of example questions
example_questions = [
    "What’s is the P/E of CVS compared to competitors",
    "Is abercrombie still a good buy",
    "Analyse CVS for me",
    "How does Arch Resources' return on equity compare to its competitors in the coal mining sector?",
    "What is the intrinsic value of Brookfield corporation",
    "What is the P/E ratio of Brookfield Corporation?",
    "Which companies, similar to Amazon, have a significant presence in both e-commerce and cloud computing services?",
    "Which tech-driven businesses, akin to Amazon, provide extensive e-commerce solutions and operate successful cloud computing divisions?",
    "Is Dynagas good stock for long run",
    "Is Taiwan semiconductor good stock in the long run",
    "Will Electric Vehicles outperform the market this year?",
    "Analyse latest earning call of Meta",
    "How does QSR.TO's market capitalization compare to its peers in the restaurant sector?",
    "How have Amazon's focus areas changed?",
    "What are the key risks investing in nvidia",
    "What is the ROI of Starbucks?",
    "What do you think of ticker LNG?",
    "Analyze CDW",
    "Is it a right time to buy Nvidia stock?",
    "Levi stock",
    "Tell me about TSLA but talk like a pirate",
    "What about BYD?",
    "What is Starbucks' return on equity (ROE) compared to its competitors in the food and beverage sector?",
    "What is McDonald's ROE compared to Starbucks in the food and beverage sector?",
    "How does Starbucks' ROE compare to Dunkin' Donuts in the coffee and bakery sector?",
    "Why the company DoubleVerify Holdings shares fell?",
    "What are the latest news for AMD?",
    "What is the latest close price of NVDA?",
    "Why is Tesla so overrated?",
    "How do Costco and Walmart compare in terms of their respective market shares in the retail industry?",
    "What are the consensus EPS forecasts for PYPL for the next 3 financial years?",
    "What is PYPL EPS in FY24, FY25 and FY26?",
    "Give me a chart of coke's P/E ratio for the last 5 years",
    "What is the stock price of Apple?",
    "Compare AMD and intel fundamentals for the last 5 years",
    "Compare the stocks of AMD and intel based on their fundamentals for the last 5 years",
    "What is the average return on equity (ROE) for AMD and Intel over the last 5 years?",
    "Do a sentiment comparison between intel and amd for the last 2 years",
    "How the options are looking for both amd and intel for the last 10 trading days",
    "How has the price-to-earnings ratio (P/E) for AMD and Intel compared over the last 10 trading days?",
    "Why intel price dropped during 2021 and 2022?",
    "How is ASTS?",
    "Is MTCH revenue growing?",
    "Tell me about amazon",
    "Will GME go up or go down today?",
    "What are the key factors influencing GME's stock price movement?",
    "Berkshire b vs voo",
    "Compare Berkshire b with voo for past 20 years performance and report me",
    "What are your thoughts on moneylion?",
    "Akon",
    "Predictions on NVIDIA for tomorrow",
    "Value of oracle",
    "Tell me about OKLA",
    "Is ASTS a good investment?",
    "Is smci good? why or why not",
    "Should I buy accenture?",
    "What is Accenture's return on equity (ROE) compared to its competitors in the IT services industry?",
    "Should I invest in Intel intc?",
    "What do you think about the ticker ENPH?",
    "What is status of apple stocks?",
    "Should I buy more apple?",
    "What is the average growth rate of HD revenue?",
    "What is the average growth rate of Home Depot revenue?",
    "I have been tracking the share price of MSI (Motorola Solutions). What are the predictions for the next 6 months?",
    "How's uber doing lately?",
    "Show me the revenue, income, price graphs for Uber",
    "Is ANGELONE a good stock to invest in?",
    "Nvidia metrics and comparables",
    "How does Nvidia's profitability compare to other semiconductor companies?",
    "How does Nvidia's market capitalization compare to other semiconductor companies?",
    "What do you think about hapag loyd?",
    "Amazon latest results",
    "Can you give me important informations for cloudlfare?",
    "What is MSFT last 3 year revenue?",
    "What is the revenue growth rate of MSFT in the last 3 years?",
    "What is asts?",
    "Future of polestar",
    "What are some key metrics of nvidia over the past few years?",
    "What is Nvidia's ROE and ROA over the past few years?",
    "Is ford a good investment right now?",
    "What are the prospects of growth for paypal?",
    "Would Costco be a good investment right now?",
    "Costco vs wallmart",
    "How do Costco and Walmart compare in terms of their respective market shares in the retail industry?",
    "How would you value costco?",
    "What is Costco's price-to-earnings ratio compared to other discount retailers?",
    "How is Ocugen performing?",
    "I meant OCGN",
    "What was Apple’s revenue last year?",
    "What is the outlook for ARM stock?",
    "What is the outlook for ARM stock?",
    "Outlook for giig stock in 2025",
    "Is SLS a good buy right now?",
    "Is AMD a good buy right now?",
    "What is happening with Tesla stock?",
    "What is the short interest on WIRE?",
    "What is the market cap of WIRE?",
    "Is AMD good to be invested now or should I vest my RSU now?",
    "What are the growth prospects for Intel in the semiconductor industry?",
    "NVDA",
    "Analyze the stock shw",
    "Zts",
    "Analyze zts",
    "Tell me about the outlook of The Qt Company, QTCOM",
    "What is the average revenue growth rate of The Qt Company in the past five years compared to its competitors in the software development industry?",
    "META vs MSFT vs NVDA?",
    "NVDA",
    "How does NVDA's market capitalization compare to its peers in the semiconductor industry?",
    "What is JPM’s net interest margin over the last 10 years?",
    "How was Q1 of Smart Sand compared to Q4 2023?",
    "Price target for NVDA?",
    "What is the price target for NVIDIA's competitors like AMD and Intel?",
    "Is lulu a good buy?",
    "Is nvidia worth buying?",
    "What is the market cap of Nvidia compared to its competitors?",
    "What stock trend is predicted for nvda?",
    "Should I buy calls on NVDA for December 2024?",
    "What do you think about SQQQ?",
    "What are the main competitors to crocs inc.?",
    "What is the long term debt of walgreen boots alliance (WBA)?",
    "What is the long term debt of CVS Health (CVS)?",
    "What is future of DAX40?",
    "What's the intrinsic value of nvidia?",
    "What is the market capitalization of Nvidia's competitors?",
    "What is the intrinsic value of Amazon?",
    "What is the intrinsic value of Walmart?",
    "What is Linde dcf value?",
    "What can you tell me about linde?",
    "What can you tell me about evvty (evolution ab)?",
    "Give me the evvty important numbers",
    "EVVTY Analysis",
    "How does EVVTY's ROE compare to its peers in the industry?",
    "What is quarterly sales and earnings of fiserv for last 2 years?",
    "What is the average quarterly sales and earnings growth rate of Fiserv and its competitors in the financial technology industry over the last 2 years?",
    "Calculate the price action movement for the last 30 days for google",
    "What are the top competitors of Albemarle in the chemical industry?",
    "What is nvidia?",
    "What is Nvidia's primary business?",
    "Current risk in Ulta stock?",
    "What is the current risk in Ulta's competitors' stocks?",
    "What is the forecast of Nano one materials?"
]


df_list=[]
for metric in metrics:
    for entity in entities:
        for example_question in example_questions:
            for _ in range(3):  # Repeat 10 times
                prompt = f""" You are an expert stock market analyst tasked with creating questions for training a model. Here are some example questions for reference:\n\n{example_questions}\n\nNow, generate 1 unique, diverse, and insightful question specifically for the metric '{metric}' and the entity '{entity}'. Ensure the question provides significant analytical depth and covers the key aspects outlined. The question should be less than 20 words and must contain both the metric '{metric}' and the entity '{entity}' exactly as specified. Use the metric '{metric}' and entity '{entity}' exactly as provided in your response, this is very very important; specifically check for this condition every single time before generating a question - like if metric is Operating Cash Flow - it should be used as it is. Start generating the questions directly without any preamble.Provide question in xml tags i.e <question>...</question>."""
                df_list.append({'Example Question': example_question,'Metric' :metric,"Entity": entity,'Prompt': prompt})


# Create a DataFrame from the list
full_df = pd.DataFrame(df_list).sample(n=25000)
full_df

prompts=[]
all_questions=full_df['Prompt'].values.tolist()

for question in  all_questions:
    prompts.append(question)

sampling_params = SamplingParams(
        temperature=0.7,
        max_tokens=100
    )

outputs = vllm_model.generate(prompts, sampling_params)

llm_output=[]
for output in outputs:
    try:
        generated_text = output.outputs[0].text
        match = re.search(r'<question>(.*?)</question>', generated_text, re.DOTALL)
        question_text = match.group(1).strip()  # Strips any leading/trailing whitespace


        llm_output.append(question_text)
    except:
        llm_output.append('')


full_df['Response'] =llm_output
display(full_df)
full_df=full_df[full_df['Response']!='']

# Define the directory path and file name
directory = '/home/ady/Stockbuzz.ai_Data/RouterNER/'
file_path = os.path.join(directory, 'Ady_User_Database_NER_Entities_Metrics_2.csv')

# Check if the directory exists, and create it if not
if not os.path.exists(directory):
    os.makedirs(directory)

# Now save the DataFrame to the CSV file
full_df.to_csv(file_path, index=False)

print(f"Synthetic questions dataset created and saved to {file_path}.")
# full_df.to_csv('/home/ady/Stocks_Guidance/StockBuzz_v2_June_24/StockBuzz_v2_June_24/AgentsTest/NER/Ady_User_Database_NER_Entities_Metrics_2.csv', index=False)# print("Synthetic questions dataset created and saved to 'Ady_Database4.csv'.")




NER Model

In [35]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

import re
import numpy as np
import torch
import pandas as pd
import time
from datasets import Dataset, load_metric
from transformers import AutoTokenizer, AutoModelForTokenClassification, TrainingArguments, Trainer, DataCollatorForTokenClassification, TrainerCallback, EarlyStoppingCallback
from transformers.trainer_utils import IntervalStrategy
import matplotlib.pyplot as plt
from collections import Counter
import torch.nn as nn

pd.set_option('display.width', 1000)

# Define the label mapping
labels = ["O", "B-ENTITY", "I-ENTITY", "B-METRIC", "I-METRIC"]
label2id = {label: i for i, label in enumerate(labels)}
id2label = {i: label for i, label in enumerate(labels)}

# Load the dataset
df_input_consolidated = pd.read_csv('/home/ady/Stockbuzz.ai_Data/RouterNER/Ady_User_Database_NER_Entities_Metrics_2.csv')

df_input_consolidated = df_input_consolidated[df_input_consolidated['Response'] != 'Error: ']
df_input_consolidated['Response'] = df_input_consolidated['Response'].str.lower()
df_input_consolidated['Metric'] = df_input_consolidated['Metric'].str.lower()
df_input_consolidated['Entity'] = df_input_consolidated['Entity'].str.lower()

train_set = int(0.8 * len(df_input_consolidated))
df_train = df_input_consolidated[:train_set][['Response', 'Metric', 'Entity']]
df_val = df_input_consolidated[train_set:][['Response', 'Metric', 'Entity']]

# Function to tokenize sentences and assign NER tags
def tag_entities_and_metrics(sentence, metric, entity):
    words = re.findall(r"\w+|[.,!?;'-]|\b's\b", sentence)
    tags = ['O'] * len(words)

    # Tagging the metric
    metric_tokens = metric.split()
    metric_len = len(metric_tokens)
    for i in range(len(words) - metric_len + 1):
        if words[i:i + metric_len] == metric_tokens:
            tags[i] = 'B-METRIC'
            for j in range(1, metric_len):
                tags[i + j] = 'I-METRIC'

    # Tagging the entity
    entity_tokens = entity.split()
    entity_len = len(entity_tokens)
    for i in range(len(words) - entity_len + 1):
        if words[i:i + entity_len] == entity_tokens:
            tags[i] = 'B-ENTITY'
            for j in range(1, entity_len):
                tags[i + j] = 'I-ENTITY'

    return words, tags

# Function to process dataframe and prepare datasets
def prepare_dataset(df):
    df['tokens_and_tags'] = df.apply(lambda row: tag_entities_and_metrics(row['Response'], row['Metric'], row['Entity']), axis=1)
    df['tokens'] = df['tokens_and_tags'].apply(lambda x: x[0])
    df['ner_tags'] = df['tokens_and_tags'].apply(lambda x: x[1])
    df = df.drop(columns=['tokens_and_tags'])
    df = df[df['ner_tags'].apply(lambda tags: not all(tag == 'O' for tag in tags))]
    df['ner_tags'] = df['ner_tags'].apply(lambda tags: [label2id[tag] for tag in tags])
    return Dataset.from_pandas(df)

# Prepare datasets
train_dataset = prepare_dataset(df_train)
val_dataset = prepare_dataset(df_val)

# Print the size of the train and validation datasets
print(f"Size of train dataset: {len(train_dataset)}")
print(f"Size of validation dataset: {len(val_dataset)}")

# Count the occurrences of each label in the training and validation sets
def count_labels(dataset):
    label_counts = Counter()
    for example in dataset:
        labels = example['ner_tags']
        for label in labels:
            label_counts[id2label[label]] += 1
    return label_counts

train_label_counts = count_labels(train_dataset)
val_label_counts = count_labels(val_dataset)

print("Training Label Counts:")
print(train_label_counts)

print("\nValidation Label Counts:")
print(val_label_counts)

# Tokenization and Alignment Functions
checkpoint = 'Jean-Baptiste/roberta-large-ner-english'
tokenizer = AutoTokenizer.from_pretrained(checkpoint)

def align_labels(labels, word_ids):
    aligned_labels = []
    prev_word_id = None
    for word_id in word_ids:
        if word_id is None:
            aligned_labels.append(-100)
        elif word_id != prev_word_id:
            aligned_labels.append(labels[word_id])
        else:
            aligned_labels.append(labels[word_id] if labels[word_id] != 0 else -100)
        prev_word_id = word_id
    return aligned_labels

def tokenize_and_align_labels(examples):
    tokenized_inputs = tokenizer(examples['tokens'], truncation=True, max_length=32, is_split_into_words=True)
    all_labels = examples['ner_tags']
    new_labels = [align_labels(labels, tokenized_inputs.word_ids(i)) for i, labels in enumerate(all_labels)]
    tokenized_inputs['labels'] = new_labels
    return tokenized_inputs

tokenized_train_dataset = train_dataset.map(tokenize_and_align_labels, batched=True, remove_columns=['Response', 'Metric', 'Entity'])
tokenized_val_dataset = val_dataset.map(tokenize_and_align_labels, batched=True, remove_columns=['Response', 'Metric', 'Entity'])

# Define the data collator
data_collator = DataCollatorForTokenClassification(tokenizer=tokenizer)

# Load metric
metric = load_metric('seqeval',trust_remote_code=True)

# Custom loss function to give higher weight to metrics
class WeightedLoss(nn.CrossEntropyLoss):
    def __init__(self, weight=None, size_average=None, ignore_index=-100, reduce=None, reduction='mean'):
        super(WeightedLoss, self).__init__(weight, size_average, ignore_index, reduce, reduction)

    def forward(self, input, target):
        if self.weight is not None:
            assert self.weight.dim() == 1
            input = input * self.weight.unsqueeze(0).expand_as(input)
        return super(WeightedLoss, self).forward(input, target)

# Custom Trainer to use the weighted loss
class CustomTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False):
        labels = inputs.get("labels")
        outputs = model(**inputs)
        logits = outputs.get("logits")
        # Define the weights, giving higher weight to METRIC labels
        class_weights = torch.tensor([0.4, 0.5, 0.5, 1.0, 1.0], device=logits.device)
        loss_fct = WeightedLoss(weight=class_weights)
        loss = loss_fct(logits.view(-1, self.model.config.num_labels), labels.view(-1))
        return (loss, outputs) if return_outputs else loss

# Function to compute metrics
def compute_metrics(p):
    predictions, labels = p
    predictions = np.argmax(predictions, axis=2)
    true_labels = [[id2label[label] for label in label_set if label != -100] for label_set in labels]
    true_predictions = [[id2label[pred] for pred, label in zip(pred_set, label_set) if label != -100] for pred_set, label_set in zip(predictions, labels)]
    results = metric.compute(predictions=true_predictions, references=true_labels, zero_division=0)

    # Calculate metrics for ENTITY
    entity_results = metric.compute(
        predictions=[[pred for pred, true in zip(pred_set, label_set) if true.startswith('B-ENTITY') or true.startswith('I-ENTITY')] for pred_set, label_set in zip(true_predictions, true_labels)],
        references=[[true for true in label_set if true.startswith('B-ENTITY') or true.startswith('I-ENTITY')] for label_set in true_labels],
        zero_division=0
    )

    # Calculate metrics for METRIC
    metric_results = metric.compute(
        predictions=[[pred for pred, true in zip(pred_set, label_set) if true.startswith('B-METRIC') or true.startswith('I-METRIC')] for pred_set, label_set in zip(true_predictions, true_labels)],
        references=[[true for true in label_set if true.startswith('B-METRIC') or true.startswith('I-METRIC')] for label_set in true_labels],
        zero_division=0
    )

    return {
        "overall_precision": results["overall_precision"],
        "overall_recall": results["overall_recall"],
        "overall_f1": results["overall_f1"],
        "overall_accuracy": results["overall_accuracy"],
        "entity_precision": entity_results["overall_precision"],
        "entity_recall": entity_results["overall_recall"],
        "entity_f1": entity_results["overall_f1"],
        "entity_accuracy": entity_results["overall_accuracy"],
        "metric_precision": metric_results["overall_precision"],
        "metric_recall": metric_results["overall_recall"],
        "metric_f1": metric_results["overall_f1"],
        "metric_accuracy": metric_results["overall_accuracy"],
    }

# Load the model
model = AutoModelForTokenClassification.from_pretrained(checkpoint, num_labels=len(labels), id2label=id2label, label2id=label2id,ignore_mismatched_sizes=True)

# Custom callback to capture loss history
class LossHistoryCallback(TrainerCallback):
    def __init__(self):
        self.losses = []
        self.eval_losses = []

    def on_log(self, args, state, control, logs=None, **kwargs):
        if logs is not None:
            if 'loss' in logs:
                self.losses.append(logs['loss'])
            if 'eval_loss' in logs:
                self.eval_losses.append(logs['eval_loss'])

loss_history_callback = LossHistoryCallback()

# Training arguments
training_args = TrainingArguments(
    output_dir='./results',
    evaluation_strategy=IntervalStrategy.STEPS,
    save_strategy="steps",
    logging_strategy="steps",
    learning_rate=1e-5,
    num_train_epochs=10,
    per_device_train_batch_size=32,
    per_device_eval_batch_size=32,    
    gradient_accumulation_steps=4,  # Accumulate gradients over 4 steps
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    eval_steps=10,
    save_steps=10,
    load_best_model_at_end=True,
    save_total_limit=1,
)

# Custom Trainer instance
trainer = CustomTrainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_train_dataset,
    eval_dataset=tokenized_val_dataset,
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    callbacks=[EarlyStoppingCallback(early_stopping_patience=2), loss_history_callback]
)

# Train the model
trainer.train()

# Save the model
trainer.save_model('/home/ady/Stockbuzz.ai_Models/RouterNER/ner_model')




Size of train dataset: 19891
Size of validation dataset: 4975


/home/ady/miniconda3/envs/vllm_env/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Training Label Counts:
Counter({'O': 322182, 'I-METRIC': 31143, 'B-ENTITY': 19886, 'B-METRIC': 16255})

Validation Label Counts:
Counter({'O': 80848, 'I-METRIC': 7635, 'B-ENTITY': 4970, 'B-METRIC': 4037})


Map: 100%|██████████| 4975/4975 [00:00<00:00, 7058.05 examples/s] 
/home/ady/miniconda3/envs/vllm_env/lib/python3.11/site-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
torch.distributed process group is initialized, but parallel_mode != ParallelMode.DISTRIBUTED. In order to use Torch DDP, launch your script with `python -m torch.distributed.launch


NER Inference

In [43]:
import time
import numpy as np
from transformers import AutoTokenizer, AutoModelForTokenClassification, pipeline

checkpoint = "ner_model"
tokenizer_ner = AutoTokenizer.from_pretrained(checkpoint)
model_ner = AutoModelForTokenClassification.from_pretrained(checkpoint)

# Initialize the NER pipeline without additional parameters
ner_model = pipeline('ner', model=model_ner, tokenizer=tokenizer_ner, aggregation_strategy='simple')

# Enhanced post-processing
def extract_entities_with_scores(example_text):
    # Tokenize the text with offset mappings
    encoding = tokenizer_ner(example_text, return_offsets_mapping=True, truncation=True, max_length=32)
    offset_mapping = encoding['offset_mapping']
    tokens = tokenizer_ner.convert_ids_to_tokens(encoding['input_ids'])
    
    # Use the pipeline directly
    ner_results = ner_model(example_text)
    # print(ner_results)

    entities = {}
    metrics = {}
    current_entity = None

    for result in ner_results:
        entity_type = result['entity_group']
        start, end = result['start'], result['end']
        score = result['score']
        word = example_text[start:end].strip()
        # print(word)

        # Check if current entity needs to be continued or started fresh
        if current_entity and current_entity['entity_group'] == entity_type and (current_entity['end'] == start or current_entity['end'] + 1 == start):
            # Continue the current entity
            current_entity['word'] += ' ' + word if current_entity['end'] + 1 == start else word
            current_entity['scores'].append(score)
            current_entity['end'] = end
        else:
            # Save the previous entity
            if current_entity:
                entity_name = current_entity['word']
                average_score = np.mean(current_entity['scores'])
                if current_entity['entity_group'] == 'ENTITY':
                    if entity_name not in entities:
                        entities[entity_name] = []
                    entities[entity_name].append(average_score)
                elif current_entity['entity_group'] == 'METRIC':
                    if entity_name not in metrics:
                        metrics[entity_name] = []
                    metrics[entity_name].append(average_score)

            # Start a new entity
            current_entity = {'entity_group': entity_type, 'word': word, 'scores': [score], 'start': start, 'end': end}

    # Append the last entity or metric if exists
    if current_entity:
        entity_name = current_entity['word']
        average_score = np.mean(current_entity['scores'])
        if current_entity['entity_group'] == 'ENTITY':
            if entity_name not in entities:
                entities[entity_name] = []
            entities[entity_name].append(average_score)
        elif current_entity['entity_group'] == 'METRIC':
            if entity_name not in metrics:
                metrics[entity_name] = []
            metrics[entity_name].append(average_score)

    return entities, metrics

# Test the model with example texts
example_texts = [
    "What is the EPS for Apple from 2023, compare it against Intel?",
    "What are the REVENUES of Amazon?",
    "What is the annual income for Microsoft vs NVDA?",
    "What is the depreciation for ShaktiPumps in 2023?",
    "What is the ttm net profits for Amazon in 2023?"
]

## Test set 
# example_texts = df_val.sample(n=5)['Response'].values.tolist()


for text in example_texts:
    entities, metrics = extract_entities_with_scores(text.lower())

    print(f"Entities and metrics and their average scores for text: '{text}'")
    print(f"Predicted Entities: {entities}")
    print(f"Predicted Metrics: {metrics}")
    print("\n" + "="*50 + "\n")


Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


Entities and metrics and their average scores for text: 'What is the EPS for Apple from 2023, compare it against Intel?'
Predicted Entities: {'apple': [0.9999647]}
Predicted Metrics: {'eps': [0.99446386]}


Entities and metrics and their average scores for text: 'What are the REVENUES of Amazon?'
Predicted Entities: {'amazon': [0.9999809]}
Predicted Metrics: {}


Entities and metrics and their average scores for text: 'What is the annual income for Microsoft vs NVDA?'
Predicted Entities: {'microsoft': [0.9999985]}
Predicted Metrics: {}


Entities and metrics and their average scores for text: 'What is the depreciation for ShaktiPumps in 2023?'
Predicted Entities: {}
Predicted Metrics: {}


Entities and metrics and their average scores for text: 'What is the ttm net profits for Amazon in 2023?'
Predicted Entities: {'amazon': [0.9999693]}
Predicted Metrics: {'tm': [0.5082908]}




In [41]:
df_input_consolidated['Metric'].value_counts()

Metric
pe ratio ttm                      1156
return on assets ttm               635
dividend yield                     615
piotroski score                    612
return on capital employed         611
price to fair-value ttm            610
net-profit margin ttm              605
debt-equity ratio ttm              603
debt ratio ttm                     598
operating profit margin ttm        597
total-debt growth                  595
retained earnings                  594
altman z score                     591
pe ratio                           589
ebit                               589
dividend yield ttm                 589
return on capital employed ttm     588
netdebt growth                     584
growth in net-income-ratio         582
dividend yield percentage ttm      581
gross profit margin ttm            578
interest coverage ttm              578
peg ratio ttm                      577
pe to growth ratio                 576
dividend payout ratio              575
ebitda growth     

Send to HF

Router

In [ ]:
## Send to Huggingface

from huggingface_hub import login
login(token="")

from huggingface_hub import upload_folder

# Define the local directory and repo details
local_model_path = "/home/ady/Stockbuzz.ai_Models/RouterNER/Router_Models/"
repo_id = "Aditiyadav/Router"  # Your Hugging Face repo

# Upload the folder directly to Hugging Face Hub
upload_folder(
    repo_id=repo_id,
    folder_path=local_model_path,  # The local directory containing the model
    commit_message="Uploading model from local directory"
)


In [ ]:
## Send to Huggingface

from huggingface_hub import login
login(token="")

from huggingface_hub import upload_folder

# Define the local directory and repo details
local_model_path = "/home/ady/Stockbuzz.ai_Models/RouterNER/SubRouter_Models/"
repo_id = "Aditiyadav/SubRouter"  # Your Hugging Face repo

# Upload the folder directly to Hugging Face Hub
upload_folder(
    repo_id=repo_id,
    folder_path=local_model_path,  # The local directory containing the model
    commit_message="Uploading model from local directory"
)


In [ ]:
## Send to Huggingface

from huggingface_hub import login
login(token="")

from huggingface_hub import upload_folder

# Define the local directory and repo details
local_model_path = "/home/ady/Stockbuzz.ai_Models/RouterNER/ner_model/"
repo_id = "Aditiyadav/NER"  # Your Hugging Face repo

# Upload the folder directly to Hugging Face Hub
upload_folder(
    repo_id=repo_id,
    folder_path=local_model_path,  # The local directory containing the model
    commit_message="Uploading model from local directory"
)
